In [258]:
import pandas as pd
import spark
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.optimizers import Adam
import numpy as np


In [259]:
#read the data

activitats = pd.read_csv('data/activitats.csv')
notes = pd.read_csv('notes_arreglat.csv')
trameses = pd.read_csv('trameses_arreglat.csv')



In [260]:

# Filter activitats to keep only entries with an activitat_id present in trameses
activitats_filtered = activitats[activitats['activitat_id'].isin(trameses['activitat_id'].unique())]

# Save or display the filtered activitats DataFrame
activitats_filtered.to_csv('activitats_filtered.csv', index=False)


In [261]:
# Create a dictionary to map each unique activitat to a unique ID
activitat_unique_id = {activitats_filtered: idx for idx, activitats_filtered in enumerate(activitats_filtered['activitat'].unique(), start=1)}

# Map the activitat values to the unique IDs in the pastas column
activitats_filtered['shared_id'] = activitats_filtered['activitat'].map(activitat_unique_id)

# Save or display the updated activitats DataFrame
activitats_filtered.to_csv('activitats_with_shared.csv', index=False)

/tmp/ipykernel_48145/3240484575.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  activitats_filtered['shared_id'] = activitats_filtered['activitat'].map(activitat_unique_id)


In [262]:
# Define the aula_id values to filter
aula_ids = [87, 92, 143, 141]

activitats_filtered = activitats_filtered[activitats_filtered['aula_id'].isin(aula_ids)]

activitats_filtered.to_csv('activitats_with_shared.csv', index=False)
# Loop through each aula_id, filter, and save as a new CSV file
for aula_id in aula_ids:
    # Filter activitats for the current aula_id
    filtered_df = activitats_filtered[activitats_filtered['aula_id'] == aula_id]
    
    # Save the filtered DataFrame to a CSV file
    filtered_df.to_csv(f'activitats_aula_{aula_id}.csv', index=False)

print("CSV files created for each specified aula_id.")


CSV files created for each specified aula_id.


In [263]:




# Merge on 'activitat_id' to add 'aula_id' from 'activitats' to 'trameses'
trameses_updated = trameses.merge(activitats_filtered[['aula_id']], on='activitat_id', how='left')
trameses_updated = trameses_updated[trameses_updated['aula_id'].notna()]
# Save the updated trameses dataset
trameses_updated.to_csv('updated_trameses.csv', index=False)


print("The aula_id has been added to the trameses dataset.")


KeyError: 'activitat_id'

In [ ]:

# Step 1: Create a dictionary of unique activities per aula_id
unique_activities_per_aula = activitats.groupby('aula_id')['activitat_id'].unique().to_dict()

# Step 2: Get unique pairs of (userid, aula_id) from the existing data
unique_user_aula_pairs = trameses[['userid', 'aula_id']].drop_duplicates()

# Step 3: Initialize a list to store new entries
new_entries = []
id = 853717


# Step 4: Iterate over each (userid, aula_id) pair
for _, row in unique_user_aula_pairs.iterrows():
    userid = row['userid']
    aula_id = row['aula_id']
    id +=1

    
    # Get all activities associated with this aula_id
    required_activities = unique_activities_per_aula.get(aula_id, [])
    
    # Get activities that this user already has for the current aula_id
    existing_activities = trameses_updated[(trameses_updated['userid'] == userid) & (trameses_updated['aula_id'] == aula_id)]['activitat_id']
    
    # Find missing activities
    missing_activities = set(required_activities) - set(existing_activities)
    
    # Add a new entry for each missing activity
    for activitat_id in missing_activities:
        new_entry = {
            'id': id,  # Generate an id if needed
            'activitat_id': activitat_id,
            'userid': userid,
            'datesubmitted': 0,  # Fill with appropriate date if needed
            'grade': 0,
            'nevaluations': 0,
            
        }
        new_entries.append(new_entry)

# Step 5: Create a DataFrame for the new entries and combine it with the existing entries
new_entries_df = pd.DataFrame(new_entries)
trameses_updated = pd.concat([trameses_updated, new_entries_df], ignore_index=True)

# Step 6: Save the updated DataFrame to a new CSV
trameses_updated.to_csv('fasdfasdfsfsdfsfs.csv', index=False)


In [ ]:
# Load datasets
activitats = activitats_filtered
# rename the column 'grade' to 'max_grade'
activitats.rename(columns={'grade': 'max_grade'}, inplace=True)


# Merge on 'activitat_id' to add 'aula_id' from 'activitats' to 'trameses'
trameses_updated = trameses_updated.merge(activitats[['activitat_id', 'aula_id','shared_id','label','max_grade']], on='activitat_id', how='left')
trameses_updated = trameses_updated[trameses_updated['aula_id'].notna()]
# Save the updated trameses dataset


print("The aula_id has been added to the trameses dataset.")


Comencem treient totes les activitats que no tenen cap tramesa associada


A continuació afegim una clau shared_id que s'encarrega de relacionar tasques identiques que es troben a cursos diferents les que no pertanyen a cap d'aquestses classes

Per últim separem per les cuatre aules de les quals tenim a disposició notes d'exàmens, i esborrem del general les que no pertanyen a cap d'aquestes aules

Added lables for diferent types of exercises

In [249]:
keywords = {
        "(OPCIONAL)": 3,

    "Problema": 1,
    "Entrega Practica": 2,
    "Entrega Pràctica": 2,
    "Lliurament Practica": 2,
    "Lliurament Pr�ctica": 2,
    "Lliurament Pràctica": 2,
    "Pr�ctica": 2,
    "RECUPERACI�": 3,
    "Recuperació": 3,
    "RECUPERACIÓ": 3,
    "Final FP": 4,
    "Exercici": 5,
    # Add more keywords and labels as needed
}

# Function to check for keywords in each activitat entry and assign a label
def label_activity(activitat):
    for keyword, label in keywords.items():
        if keyword in activitat:
            return label
    return 0  # Default label if no keywords match

# Apply the function to create a new 'label' column
activitats_filtered['label'] = activitats_filtered['activitat'].apply(label_activity)
activitats_filtered.to_csv('activitats_with_shared.csv', index=False)


In [250]:

# Load datasets
activitats = activitats_filtered
# rename the column 'grade' to 'max_grade'
activitats.rename(columns={'grade': 'max_grade'}, inplace=True)


# Merge on 'activitat_id' to add 'aula_id' from 'activitats' to 'trameses'
trameses_updated = trameses.merge(activitats[['activitat_id', 'aula_id','shared_id','label','max_grade']], on='activitat_id', how='left')
trameses_updated = trameses_updated[trameses_updated['aula_id'].notna()]
# Save the updated trameses dataset
trameses_updated.to_csv('updated_trameses.csv', index=False)


print("The aula_id has been added to the trameses dataset.")


The aula_id has been added to the trameses dataset.


/tmp/ipykernel_48145/2301925972.py:46: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  trameses_updated = pd.concat([trameses_updated, new_entries_df], ignore_index=True)


In [252]:
# Create a dictionary to map each unique activitat to a unique ID
activitat_unique_id = {activitats_filtered: idx for idx, activitats_filtered in enumerate(activitats_filtered['activitat'].unique(), start=1)}

# Map the activitat values to the unique IDs in the pastas column
activitats_filtered['shared_id'] = activitats_filtered['activitat'].map(activitat_unique_id)

# Save or display the updated activitats DataFrame
activitats_filtered.to_csv('activitats_with_shared.csv', index=False)

In [253]:

# Load datasets
activitats = activitats_filtered
# rename the column 'grade' to 'max_grade'
activitats.rename(columns={'grade': 'max_grade'}, inplace=True)


# Merge on 'activitat_id' to add 'aula_id' from 'activitats' to 'trameses'
trameses_updated = trameses_updated.merge(activitats[['activitat_id', 'aula_id','shared_id','label','max_grade']], on='activitat_id', how='left')
trameses_updated = trameses_updated[trameses_updated['aula_id'].notna()]
# Save the updated trameses dataset


print("The aula_id has been added to the trameses dataset.")


KeyError: 'aula_id'

In [242]:
keywords = {
        "(OPCIONAL)": 3,

    "Problema": 1,
    "Entrega Practica": 2,
    "Entrega Pràctica": 2,
    "Lliurament Practica": 2,
    "Lliurament Pr�ctica": 2,
    "Lliurament Pràctica": 2,
    "Pr�ctica": 2,
    "RECUPERACI�": 3,
    "Recuperació": 3,
    "RECUPERACIÓ": 3,
    "Final FP": 4,
    "Exercici": 5,
    # Add more keywords and labels as needed
}

# Function to check for keywords in each activitat entry and assign a label
def label_activity(activitat):
    for keyword, label in keywords.items():
        if keyword in activitat:
            return label
    return 0  # Default label if no keywords match

# Apply the function to create a new 'label' column
activitats_filtered['label'] = activitats_filtered['activitat'].apply(label_activity)
activitats_filtered.to_csv('activitats_with_shared.csv', index=False)
trameses_updated.to_csv('updated_trameses.csv', index=False)


In [243]:
# Load datasets
activitats = activitats_filtered
# rename the column 'grade' to 'max_grade'
activitats.rename(columns={'grade': 'max_grade'}, inplace=True)


# Merge on 'activitat_id' to add 'aula_id' from 'activitats' to 'trameses'
trameses_updated = trameses_updated.merge(activitats[['activitat_id', 'aula_id','shared_id','label','max_grade']], on='activitat_id', how='left')
trameses_updated.to_csv('njkefgkljdsfakj.csv', index=False)

trameses_updated = trameses_updated[trameses_updated['aula_id'].notna()]
# Save the updated trameses dataset


print("The aula_id has been added to the trameses dataset.")

KeyError: 'aula_id'

In [215]:

# Initialize a dictionary to store data for each (userid, aula_id) pair
user_data = {}

# Iterate through each row in trameses
max_len = 0
for _, row in trameses_updated.iterrows():
    user_id = row['userid']
    aula_id = row['aula_id']
    grade = row['grade']
    max_grade = row['max_grade']
    shared_id = row['shared_id']
    nevaluations = row['nevaluations']
    label = row['label']
    datesubmitted = row['datesubmitted']
    
    # Use (userid, aula_id) tuple as a unique key in the dictionary
    key = (user_id, aula_id)
    
    # Initialize the list for this user-aula pair if not already created
    if key not in user_data:
        user_data[key] = []
    
    # Append the grade, datesubmitted, and aula_id to the list for this user-aula pair
    user_data[key].append([grade/max_grade,datesubmitted,shared_id, nevaluations,label]
                          
    )
    if len(user_data[key]) > max_len:
        max_len = len(user_data[key])

print(max_len)

171


In [216]:
# Flatten the user_data dictionary into an array
user_data_array = []
for key, values in user_data.items():
    user_data_array.append(np.array(values))
print(user_data_array[0])




# Create a new array to store the F_Grade for each (userid, aula_id) combination
f_grade_array = []

# Iterate through the user_data_array and fetch the corresponding F_Grade from notes
for key, values in user_data.items():
    userid, aula_id = key[0], key[1]
    f_grade = notes.loc[(notes['userid'] == userid) & (notes['aula_id'] == aula_id), 'F_Grade']
    if not f_grade.empty:
        f_grade_array.append(f_grade.values[0])
    else:
        f_grade_array.append(np.nan)  # Append NaN if no F_Grade is found
    last = key
f_grade_array = np.array(f_grade_array)

print("User Data Array:")
print(user_data_array)
print("F_Grade Array:")
print(f_grade_array)



[[1.00000000e+00 1.66307478e+09 1.00000000e+00 1.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66307624e+09 2.00000000e+00 1.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66341510e+09 3.00000000e+00 2.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66357956e+09 4.00000000e+00 3.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66358372e+09 5.00000000e+00 1.20000000e+01
  1.00000000e+00]
 [1.00000000e+00 1.66358409e+09 6.00000000e+00 3.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66358142e+09 7.00000000e+00 1.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66358205e+09 8.00000000e+00 1.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66343362e+09 9.00000000e+00 1.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66343426e+09 1.00000000e+01 2.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66343487e+09 1.10000000e+01 2.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66358256e+09 1.20000000e+01 1.00000000e+00
  1.00000000e+00]
 [1.00000000e+00 1.66358352e+09 1.300000

User Data Array:
[array([[1.00000000e+00, 1.66307478e+09, 1.00000000e+00, 1.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66307624e+09, 2.00000000e+00, 1.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66341510e+09, 3.00000000e+00, 2.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66357956e+09, 4.00000000e+00, 3.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66358372e+09, 5.00000000e+00, 1.20000000e+01,
        1.00000000e+00],
       [1.00000000e+00, 1.66358409e+09, 6.00000000e+00, 3.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66358142e+09, 7.00000000e+00, 1.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66358205e+09, 8.00000000e+00, 1.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66343362e+09, 9.00000000e+00, 1.00000000e+00,
        1.00000000e+00],
       [1.00000000e+00, 1.66343426e+09, 1.00000000e+01, 2.00000000e+00,
        1.00000000e+00],
       [1.00

In [217]:
print(len(user_data_array))


704


In [218]:
# Find the indices where f_grade_array is NaN
nan_indices = np.isnan(f_grade_array)

# Filter out the elements in user_data_array and f_grade_array where the indices match NaN
user_data_array_filtered = user_data_array[~nan_indices]
f_grade_array_filtered = f_grade_array[~nan_indices]

print(len(user_data_array_filtered))
print(len(f_grade_array_filtered))
print(f_grade_array_filtered[-1])

TypeError: only integer scalar arrays can be converted to a scalar index

In [125]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split

# Example array

# Split the array into 80% train and 20% test
X_train, X_test, y_train, y_test = train_test_split(user_data_array_filtered, f_grade_array_filtered, test_size=0.2, random_state=42)

import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Example jagged array (list of lists with varying lengths)

# Pad sequences to a fixed length (e.g., max length of 4)
padded_data = pad_sequences(X_train, padding='post')
prin
print("Padded Data:\n", padded_data)

# Convert to Tensor for model training
padded_data_tensor = tf.convert_to_tensor(padded_data, dtype=tf.float32)


# Hyperparameters
n_timesteps = max_len   # Number of timesteps (length of input sequence)
n_features = 5     # Number of features in each tuple (mark, date, id)
embedding_dim = 4  # Dimension for embedding the ID



# Define a "beefier" RNN model
model = Sequential([
    # First LSTM layer with more units and return sequences
    LSTM(128, return_sequences=True),
    Dropout(0.3),  # Dropout layer to prevent overfitting

    # Second LSTM layer
    LSTM(64, return_sequences=True),
    Dropout(0.3),

    # Third LSTM layer
    LSTM(32, return_sequences=False),
    Dropout(0.3),

    # Fully connected layers
    Dense(64, activation='relu'),
    Dropout(0.3),  # Dropout layer for regularization

    Dense(32, activation='relu'),
    Dense(1)  # Output layer for single prediction
])

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.001), loss='mse', metrics=['mae'])

model.summary()


# Compile the model
model.compile(optimizer=Adam(learning_rate=0.001), loss='mse', metrics=['mae'])

# Summary of the model
model.summary()

# Train the model
history = model.fit(padded_data, y_train, epochs=20, batch_size=8, validation_split=0.2)


Padded Data:
 [[[         1 1663091547          1          1          1]
  [         1 1663091791          2          2          1]
  [         1 1663236078          3          1          1]
  ...
  [         0          0          0          0          0]
  [         0          0          0          0          0]
  [         0          0          0          0          0]]

 [[         1 1694883935          1          1          1]
  [         1 1694884046          2          1          1]
  [         1 1695032026          3          2          1]
  ...
  [         0          0          0          0          0]
  [         0          0          0          0          0]
  [         0          0          0          0          0]]

 [[         1 1663021419          1          1          1]
  [         1 1663086053          2          1          1]
  [         1 1663266727          3          2          1]
  ...
  [         0          0          0          0          0]
  [         0       

Model: "sequential_9"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm_22 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_24 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_23 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_25 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_24 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_26 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_24 (Dense)                │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_27 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_25 (Dense)                │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_26 (Dense)                │ ?                      │   0 (unbuilt) │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm_22 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_24 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_23 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_25 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_24 (LSTM)                  │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_26 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_24 (Dense)                │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_27 (Dropout)            │ ?                      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_25 (Dense)                │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_26 (Dense)                │ ?                      │   0 (unbuilt) │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 0 (0.00 B)

Epoch 1/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 6s 62ms/step - loss: 23.4555 - mae: 4.1109 - val_loss: 8.7557 - val_mae: 2.5520
Epoch 2/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 8.8127 - mae: 2.4645 - val_loss: 8.8747 - val_mae: 2.5519
Epoch 3/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 8.8580 - mae: 2.5008 - val_loss: 8.7800 - val_mae: 2.5504
Epoch 4/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 8.4761 - mae: 2.4608 - val_loss: 9.1551 - val_mae: 2.5601
Epoch 5/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 8.5418 - mae: 2.4658 - val_loss: 8.9702 - val_mae: 2.5482
Epoch 6/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 7.6280 - mae: 2.2745 - val_loss: 8.5903 - val_mae: 2.5085
Epoch 7/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 7.9482 - mae: 2.3552 - val_loss: 7.8617 - val_mae: 2.3949
Epoch 8/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 51ms/step - loss: 7.5865 - mae: 2.2663 - val_loss: 7.8422 - val_mae: 2.4164
Epoch 9/20
56/56 ━━━━━━━━━━━━━━━━━━━━ 3s 53ms/step - loss: 6.57

In [126]:
import matplotlib.pyplot as plt

# Make predictions on the test set
y_pred = model.predict(X_test)

# Plotting the true vs. predicted values
plt.figure(figsize=(10, 6))

# Scatter plot of actual vs. predicted marks
plt.scatter(y_test, y_pred, color='blue', label='Predicted vs Actual')
plt.plot([min(y_test), max(y_test)], [min(y_test), max(y_test)], color='red', linestyle='--', label='Perfect Prediction')

# Labels and title
plt.xlabel("Actual Final Marks")
plt.ylabel("Predicted Final Marks")
plt.title("Actual vs Predicted Final Marks")
plt.legend()
plt.show()


ValueError: Failed to convert a NumPy array to a Tensor (Unsupported object type numpy.ndarray).

In [12]:
# Predicting a final mark for a new sequence
predicted_final_mark = model.predict(test)
print("Predicted Final Mark:", predicted_final_mark)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step
Predicted Final Mark: [[0.6319191]]


In [13]:
shared_id
#aula_id
#date
grade
label

np.float64(nan)

In [14]:
trameses.groupby(['A','B']).size().reset_index()

KeyError: 'A'